# How to Apply MLRun on Existing Code?

In this tutorial we will showcase how easy it is to apply MLRun on your existing code. **With only 7 lines of code**, you will get:
* Experiment tracking - Track every single run of your experiment to learn what yielded the best results.
* Automatic Logging - Log datasets, metrics results and plots with one line of code. MLRun will take care for all the rest.
* Parameterization - Enable running your code with different parameters, run hyperparameters tuning and get the most out of your code.
* Resource management - Control the amount of resources available for your experiment.

We will use this [kaggle code](https://www.kaggle.com/code/jsylas/python-version-of-top-ten-rank-r-22-m-2-88/script) by [Sylas](https://www.kaggle.com/jsylas) as an example, part of the competition [New York City Taxi Fare Prediction](https://www.kaggle.com/competitions/new-york-city-taxi-fare-prediction/overview/description).

## 1. Get the Data

You may download the original data from [kaggle](https://www.kaggle.com/code/jsylas/python-version-of-top-ten-rank-r-22-m-2-88/data?select=train.csv), but as it is 5.7GB in size, we sampled it for demonstration purposes. To check our sampled data, you may download it from here: [training set](https://s3.us-east-1.wasabisys.com/iguazio/data/nyc-taxi/train.csv), [testing set](https://s3.us-east-1.wasabisys.com/iguazio/data/nyc-taxi/test.csv)

Keep in mind that because we will use MLRun's `DataItem` to pass the datasets, it will be downloaded automatically, so download them only if you wish to look inside.

## 2. Code Review

We will use the original code with the most minimum changes required to apply MLRun to it. The code itself is stragiht forward:
1. Read the training data and perform feature engineering on it to preprocess it for training.
2. Train a LightGBM regression model using LightGBM's `train` function.
3. Read the testing data and save the contest expected submission file.

You can [**Download the `script.py` file**](./script.py), or copy paste it from here:
````{dropdown} Show code
   ```{literalinclude} ./script.py
   :language: python3
   ```
````

We will focus on reviewing the changes / additions made to the original code to apply MLRun on top of it. **We added / replaced 7 lines of code** you can see in the tabs below:

### Initialization

#### Imports

On lines 9-10, we added 2 imports:
* `mlrun` - Import MLRun of course.
* `apply_mlrun` - We'll use the `apply_mlrun` function from MLRun's frameworks, a sub-package for common ML/DL frameworks integrations with MLRun. 

```python
import mlrun
from mlrun.frameworks.lgbm import apply_mlrun
```

#### MLRun Context

To get parameters and inputs into the code, we need to get MLRun's context. We can do so by using the function `get_or_create_ctx`.

Line 13:
```python
context = mlrun.get_or_create_ctx("apply-mlrun-tutorial")
```

#### Get Training Set

In the original code the training set was read from local file. Now we wish to get it from the user who will run the code. We'll use the context to get the `"training_set"` input using the `get_input` method. To not change the original logic, we also included default path for when the training set was not provided by the user.

Line 16:
```python
train_df = context.get_input("train_set", "./train.csv").as_df()  
# Instead of: `train_df =  pd.read_csv('./train.csv')`
```


### Apply MLRun

We'll now use the `apply_mlrun` function from MLRun's LightGBM framework integration. MLRun will automatically wrap the LightGBM module and enable automatic logging and evaluation.

Line 219:
```python
apply_mlrun(context=context)
```

### Logging the dataset

Similar to the way we got the training set, we will get the test dataset as an input from the MLRun conte

Line 235:
```python
test_df = context.get_input("test_set", "./test.csv").as_df()
# Instead of: `test_df =  pd.read_csv('./test.csv')`
```

#### Save the Submission

Finally, instead of saving the result locally, we will log the submission to MLRun.

Line 267:
```python
context.log_dataset(key="taxi_fare_submission", df=submission, format="csv")  
# Instead of: `submission.to_csv('taxi_fare_submission.csv',index=False)`
```


## 3. Run the Script with MLRun

We will now run the script and see MLRun in action.

In [1]:
import mlrun
import os

### 3.1. Create a Project

We will create a project using the function `get_or_create_project`. To read more about MLRun projects, click [here](https://docs.mlrun.org/en/latest/projects/project.html)

In [2]:
project = mlrun.get_or_create_project(name="apply-mlrun-tutorial", context="./", user_project=True)

> 2022-08-24 10:48:13,115 [info] loaded project apply-mlrun-tutorial from MLRun DB


### 3.2. Create a Function

We will create an MLRun function using the function `code_to_function`. To read more about MLRun functions, click [here](https://docs.mlrun.org/en/latest/concepts/functions-concepts.html)

In [3]:
script_function = mlrun.code_to_function(
    filename="./script.py",
    name="apply-mlrun-tutorial-function",
    kind="job",
    image="mlrun/ml-models"
)
if not os.environ.get('MLRUN_CE'): # mount if not on community edition
    script_function.apply(mlrun.platforms.auto_mount())

### 3.3. Run the Function

Now we can run the function, providing it with the inputs we desire. We will use the datasets links to send them over to the function. MLRun will download and read them into `pd.DataFrame` automatically.

In [4]:
script_run = script_function.run(
    inputs={
        "train_set": "https://s3.us-east-1.wasabisys.com/iguazio/data/nyc-taxi/train.csv",
        "test_set": "https://s3.us-east-1.wasabisys.com/iguazio/data/nyc-taxi/test.csv"
    },
)

> 2022-08-24 10:48:13,211 [warning] it is recommended to use k8s secret (specify secret_name), specifying the aws_access_key/aws_secret_key directly is unsafe
> 2022-08-24 10:48:13,217 [info] starting run apply-mlrun-tutorial-function uid=89c26c07b12d40c2903fba400d3988c1 DB=http://mlrun-api:8080
> 2022-08-24 10:48:13,390 [info] Job is running in the background, pod: apply-mlrun-tutorial-function-nlv7d
> 2022-08-24 10:48:18,816 [info] handler was not provided running main (script.py)
> 2022-08-24 10:48:24,814 [info] logging run results to: http://mlrun-api:8080
   pickup_longitude  pickup_latitude  ...  distance   bearing
0         -1.288826         0.710721  ...  1.030764 -2.918897
1         -1.291824         0.710546  ...  8.450134 -0.375217
2         -1.291242         0.711418  ...  1.389525  2.599961
3         -1.291319         0.710927  ...  2.799270  0.133905
4         -1.290987         0.711536  ...  1.999157 -0.502703

[5 rows x 17 columns]
[LightGBM] [Warning] bagging_fraction 

> 2022-08-24 10:50:17,557 [info] run executed, status=completed


## 4. Review Outputs

We can see what outputs MLRun automatic logging and evaluation yielded by calling the `outputs` property on the run object:

In [5]:
script_run.outputs

{'valid_0_rmse': 3.905279481685527,
 'valid_0_rmse_plot': 's3://mlrun/apply-mlrun-tutorial-function/0/valid_0_rmse_plot.html',
 'valid_0-feature-importance': 's3://mlrun/apply-mlrun-tutorial-function/0/valid_0-feature-importance.html',
 'valid_0': 'store://artifacts/apply-mlrun-tutorial-jovyan/apply-mlrun-tutorial-function_valid_0:89c26c07b12d40c2903fba400d3988c1',
 'model': 'store://artifacts/apply-mlrun-tutorial-jovyan/model:89c26c07b12d40c2903fba400d3988c1',
 'taxi_fare_submission': 'store://artifacts/apply-mlrun-tutorial-jovyan/apply-mlrun-tutorial-function_taxi_fare_submission:89c26c07b12d40c2903fba400d3988c1'}

MLRun **automatically detects all the metrics calculated** and collect the data along the training. Here there was one validation set named `valid_0` and the RMSE metric was calculated on it. You can see the RMSE values per iteration plot and the final score including the features importance plot.

You can explore the different artifacts by calling the `artifact` function like so:

In [6]:
script_run.artifact('valid_0_rmse_plot').show()

In [7]:
script_run.artifact('valid_0-feature-importance').show()

And of course, you can see the submission that was logged as well:

In [8]:
script_run.artifact('taxi_fare_submission').show()

key  fare_amount
0     2015-01-27 13:08:24.0000002    10.281408
1     2015-01-27 13:08:24.0000003    11.019641
2     2011-10-08 11:53:44.0000002     4.898061
3     2012-12-01 21:12:12.0000002     7.758042
4     2012-12-01 21:12:12.0000003    15.298775
...                           ...          ...
9909  2015-05-10 12:37:51.0000002     9.117569
9910  2015-01-12 17:05:51.0000001    10.850885
9911  2015-04-19 20:44:15.0000001    55.048856
9912  2015-01-31 01:05:19.0000005    20.110280
9913  2015-01-18 14:06:23.0000006     7.081041

[9914 rows x 2 columns]